In [1]:
import pandas as pd
import plotly.express as px
import json
import requests
import numpy as np

In [2]:
df = pd.read_csv("Defunciones_Mex_2023.csv")
df.head()

/var/folders/nz/ntbk00f557jfbvm0fp_h8yyh0000gn/T/ipykernel_56119/2643048758.py:1: DtypeWarning: Columns (72) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv("Defunciones_Mex_2023.csv")


ent_regis  mun_regis                    tloc_regis  loc_regis  \
0          1          1  500 000 a 999 999 habitantes          1   
1          1          1  500 000 a 999 999 habitantes          1   
2          1          1  500 000 a 999 999 habitantes          1   
3          1          1  500 000 a 999 999 habitantes          1   
4          1          1  500 000 a 999 999 habitantes          1   

        ent_resid  mun_resid                    tloc_resid  loc_resid  \
0       Zacatecas         44      5 000 a 9 999 habitantes          1   
1  Aguascalientes          1  500 000 a 999 999 habitantes          1   
2  Aguascalientes          1  500 000 a 999 999 habitantes          1   
3  Aguascalientes          1  500 000 a 999 999 habitantes          1   
4         Jalisco         53            1 a 999 habitantes       7777   

        ent_ocurr  mun_ocurr  ...       complicaro  dia_cert   mes_cert  \
0  Aguascalientes          1  ...  No especificada        18  Diciembre   
1  Aguascalientes          1  ...  No especificada        12  Diciembre   
2  Aguascalientes          1  ...  No especificada        17  Diciembre   
3  Aguascalientes          1  ...  No especificada         1      Enero   
4  Aguascalientes          1  ...        No aplica        22  Diciembre   

  anio_cert maternas ent_ocules  mun_ocules loc_ocules razon_m dis_re_oax  
0      2022      NaN         88         888       8888     NaN        999  
1      2022      NaN         88         888       8888     NaN        999  
2      2022      NaN         88         888       8888     NaN        999  
3      2023      NaN         88         888       8888     NaN        999  
4      2022      NaN         88         888       8888     NaN        999  

[5 rows x 74 columns]

In [9]:
def prepare_data(sql_result_df):
    # Mapeo de nombres de estados a códigos (mantener el mismo mapeo)
    state_codes = {
        'Ciudad de México': 'MX-CMX', 'Michoacán de Ocampo': 'MX-MIC',
        'Sinaloa': 'MX-SIN', 'Durango': 'MX-DUR', 'Guerrero': 'MX-GRO',
        'Chiapas': 'MX-CHP', 'Guanajuato': 'MX-GUA', 'Hidalgo': 'MX-HID',
        'Nayarit': 'MX-NAY', 'Coahuila de Zaragoza': 'MX-COA',
        'Chihuahua': 'MX-CHH', 'Morelos': 'MX-MOR',
        'Veracruz de Ignacio de la Llave': 'MX-VER', 'Yucatán': 'MX-YUC',
        'Colima': 'MX-COL', 'Campeche': 'MX-CAM', 'Tabasco': 'MX-TAB',
        'Oaxaca': 'MX-OAX', 'San Luis Potosí': 'MX-SLP',
        'Aguascalientes': 'MX-AGU', 'Baja California Sur': 'MX-BCS',
        'Puebla': 'MX-PUE', 'Nuevo León': 'MX-NLE', 'Tamaulipas': 'MX-TAM',
        'Zacatecas': 'MX-ZAC', 'Tlaxcala': 'MX-TLA', 'Querétaro': 'MX-QUE',
        'Jalisco': 'MX-JAL', 'Quintana Roo': 'MX-ROO', 'Sonora': 'MX-SON',
        'México': 'MX-MEX', 'Baja California': 'MX-BCN'
    }

    # Renombrar columnas y añadir códigos de estado
    df = sql_result_df.rename(columns={'ent_mat': 'estado', 'count(1)': 'muertes'})
    df['id'] = df['estado'].map(state_codes)

    # Calcular rangos dinámicos basados en los cuartiles de los datos
    q1, q2, q3 = np.percentile(df['muertes'], [25, 50, 75])

    # Categorizar los valores usando rangos dinámicos
    df['categoria'] = pd.cut(
        df['muertes'],
        bins=[0, q1, q2, q3, float('inf')],
        labels=['Very Low', 'Low', 'Mid', 'High']
    )

    return df, [q1, q2, q3]

def create_interactive_map(df, year="2022", ranges=None):
    # Obtener el GeoJSON
    url = "https://raw.githubusercontent.com/angelnmara/geojson/master/mexicoHigh.json"
    geojson_data = requests.get(url).json()

    # Crear el mapa interactivo con escala de color dinámica
    fig = px.choropleth(
        df,
        geojson=geojson_data,
        locations='id',
        color='muertes',
        hover_data={
            'estado': True,
            'categoria': True,
            'muertes': ':,',
            'id': False
        },
        color_continuous_scale=[
            [0, 'rgba(255, 255, 255, 0.2)'],
            [0.25, 'rgba(222, 255, 13, 0.3)'],
            [0.5, 'rgba(222, 255, 13, 0.5)'],
            [0.75, 'rgba(222, 255, 13, 0.7)'],
            [1, 'rgba(222, 255, 13, 1.0)']
        ],
        featureidkey='properties.id',
        range_color=[df['muertes'].min(), df['muertes'].max()]
    )

    # Personalizar el diseño
    fig.update_geos(
        showcoastlines=True,
        coastlinecolor="rgba(255, 255, 255, 0.5)",
        showland=True,
        landcolor="#15110F",
        showcountries=True,
        countrycolor="rgba(255, 255, 255, 0.5)",
        showframe=False,
        projection_scale=2,
        center=dict(lat=24, lon=-102)
    )

    # Preparar los valores y textos para la barra de color
    if ranges:
        min_val = df['muertes'].min()
        max_val = df['muertes'].max()
        tickvals = [min_val] + ranges + [max_val]
        # Formatear los números con separadores de miles
        ticktext = [f'{int(val):,}' for val in tickvals]

    fig.update_layout(
        paper_bgcolor='#15110F',
        plot_bgcolor='#15110F',
        geo=dict(
            bgcolor='#15110F',
            lakecolor='#15110F',
        ),
        title=dict(
            text=f'Deaths per State {year}',
            font=dict(size=20, color='white', family='Arial Black'),
            x=0.5,
            y=0.95
        ),
        coloraxis_colorbar=dict(
            title='Number of<br>deaths',
            tickfont=dict(color='white', size=12),
            titlefont=dict(color='white', size=14),
            thickness=20,
            len=0.75,
            bgcolor='rgba(255, 255, 255, 0.1)',
            bordercolor='rgba(255, 255, 255, 0.2)',
            ticktext=ticktext if ranges else None,
            tickvals=tickvals if ranges else None,
            tickmode='array' if ranges else 'auto'
        ),
        hoverlabel=dict(
            bgcolor='rgba(50, 50, 50, 0.9)',
            font_size=14,
            font_color='white',
            bordercolor='rgba(255, 255, 255, 0.2)'
        ),
        margin=dict(l=0, r=0, t=50, b=0)
    )

    fig.update_traces(
        hovertemplate="<b>%{customdata[0]}</b><br>" +
                     "Category: %{customdata[1]}<br>" +
                     "# of Deaths: %{customdata[2]}<extra></extra>"
    )

    return fig

In [10]:
# First, convert value counts to a DataFrame with the right format
df_muertes = df["ent_ocurr"].value_counts().reset_index()
df_muertes.columns = ['ent_mat', 'count(1)']  # Rename to match expected format

# Now prepare the data and create map
df_all, ranges_all = prepare_data(df_muertes)
fig_all = create_interactive_map(df_all, "2020-2023", ranges_all)
fig_all.show()

In [7]:
df["ent_ocurr"].value_counts()

AttributeError: 'Series' object has no attribute 'toPandas'

In [12]:
# First, convert value counts to a DataFrame with the right format
df_muertes_infarto = df[df["lista_mex"] == "Infarto agudo del miocardio"]
df_muertes_infarto = df_muertes_infarto["ent_ocurr"].value_counts().reset_index()
df_muertes_infarto.columns = ['ent_mat', 'count(1)']  # Rename to match expected format

# Now prepare the data and create map
df_all, ranges_all = prepare_data(df_muertes_infarto)
fig_all = create_interactive_map(df_all, "Heath attack", ranges_all)
fig_all.show()

In [11]:
df["lista_mex"].value_counts()

lista_mex
Infarto agudo del miocardio                  131203
Diabetes mellitus                            110059
Neumonía                                      33454
Agresiones (homicidios)                       32252
Otras enfermedades del hígado                 26883
                                              ...  
Deformidades adquiridas de los miembros           1
Hidrocele y espermatocele                         1
Otras enfermedades debidas a espiroquetas         1
Fiebre paratifoidea                               1
Aborto espontáneo                                 1
Name: count, Length: 319, dtype: int64

In [16]:
# First, convert value counts to a DataFrame with the right format
df_muertes_diabetes = df[df["lista_mex"] == "Diabetes mellitus"]
df_muertes_diabetes = df_muertes_diabetes["ent_ocurr"].value_counts().reset_index()
df_muertes_diabetes.columns = ['ent_mat', 'count(1)']  # Rename to match expected format

# Now prepare the data and create map
df_all, ranges_all = prepare_data(df_muertes_diabetes)
fig_all = create_interactive_map(df_all, "Diabetes", ranges_all)
fig_all.show()

In [14]:
# First, convert value counts to a DataFrame with the right format
df_muertes_neumonia = df[df["lista_mex"] == "Neumonía"]
df_muertes_neumonia = df_muertes_neumonia["ent_ocurr"].value_counts().reset_index()
df_muertes_neumonia.columns = ['ent_mat', 'count(1)']  # Rename to match expected format

# Now prepare the data and create map
df_all, ranges_all = prepare_data(df_muertes_neumonia)
fig_all = create_interactive_map(df_all, "Neumonia", ranges_all)
fig_all.show()

In [17]:
# First, convert value counts to a DataFrame with the right format
df_muertes_homicidios = df[df["lista_mex"] == "Agresiones (homicidios)"]
df_muertes_homicidios = df_muertes_homicidios["ent_ocurr"].value_counts().reset_index()
df_muertes_homicidios.columns = ['ent_mat', 'count(1)']  # Rename to match expected format

# Now prepare the data and create map
df_all, ranges_all = prepare_data(df_muertes_homicidios)
fig_all = create_interactive_map(df_all, "Homicides", ranges_all)
fig_all.show()

In [19]:
# First, convert value counts to a DataFrame with the right format
df_muertes_higado = df[df["lista_mex"] == "Otras enfermedades del hígado"]
df_muertes_higado = df_muertes_higado["ent_ocurr"].value_counts().reset_index()
df_muertes_higado.columns = ['ent_mat', 'count(1)']  # Rename to match expected format

# Now prepare the data and create map
df_all, ranges_all = prepare_data(df_muertes_higado)
fig_all = create_interactive_map(df_all, "Liver", ranges_all)
fig_all.show()
